# **토지 가치 예측가에 대한 분석 LLM**
- Author: Kim Dohwan [@ehghks021203](https://github.com/ehghks021203)
- Date: 2024.04.25. ~
- Description: XGBoost 모델을 통해 산정된 예측가를 논리적으로 분석하는 LLM 모델을 개발합니다.
------

## **Overview**

XGBoost 알고리즘을 통해 학습한 모델을 사용하여 토지의 가격을 예측하고, 예측가에 대해 왜 그렇게 평가가 되었는지에 대한 설명 내용을 LLM 모델(Gemini 1.5 pro)을 사용하여 생성합니다.


In [1]:
import os
import sys
sys.path.append(os.path.dirname(os.path.abspath('')))
# ignore warning
import warnings
warnings.filterwarnings('ignore')

## **1. Model load**

사전에 학습된 모델을 불러옵니다.

In [2]:
import xgboost as xgb

loaded_model = xgb.XGBRegressor()
loaded_model.load_model("../Models/xgboost_model.json")

## **2. Create Land Feature**

모델 예측에 사용될 토지 특징을 생성합니다. 토지의 PNU 고유 코드와 기준년월을 입력하면 해당 기준에 알맞는 토지 특징이 생성됩니다.

2024년도 토지특성정보 데이터가 아직 모두 생성된 것이 아니기 때문에 2023년도 12월을 기준으로 토지 평가를 진행하였습니다.

In [3]:
import src.data.make_input_data as mid
import src.data.convert_code as cc
    
target_pnu = "1147010100109370018"
target_date = "202312"
print("예측하고자 하는 토지 주소:", cc.code2addr(target_pnu))
target_land = mid.make(target_pnu, target_date)

예측하고자 하는 토지 주소: 서울특별시 양천구 신정동 937-18
https://ecos.bok.or.kr/api/StatisticSearch/S961AZMHCKYULG41M1WJ/json/kr/1/100/404Y014/M/202312/202312/*AA/?/?/?
https://ecos.bok.or.kr/api/StatisticSearch/S961AZMHCKYULG41M1WJ/json/kr/1/100/404Y014/M


SystemExit: Failed to fetch producer price index data from the API.

In [6]:
%tb

SystemExit: Failed to fetch producer price index data from the API.

In [4]:
target_feature = {}
for feature in loaded_model.feature_names_in_:
    if not feature in target_land.keys():
        if feature.split("_")[0] == "Sido":
            target_feature[feature] = feature.split("_")[1] == target_land["PNU"][0:2]
        elif feature.split("_")[0] == "LandUsePlans":
            target_feature[feature] = feature.split("_")[1] in target_land["LandUsePlans"].split("/")
        else:
            target_feature[feature] = feature.split("_")[1] in target_land[feature.split("_")[0]]
    else:
        target_feature[feature] = target_land[feature]

생성된 딕셔너리를 `DataFrame` 형태로 바꿔주고 가격 예측을 진행합니다.

In [5]:
import pandas as pd

target_x = pd.DataFrame.from_dict(data=[target_feature], orient="columns", dtype=float)
target_predict = loaded_model.predict(target_x)

print(f"토지 예측가: {target_predict[0]:,.0f}원/㎡당")

토지 예측가: 6,329,059원/㎡당


## **3. Create Text by Decision Tree**
### **3-1. Prompt generation**

모델에 넣어줄 프롬프트를 생성합니다.

프롬프트는 크게 세 가지의 정보를 담고 있습니다.

<br/>

**1. 역할 부여:**

모델에게 어떤 역할로 텍스트를 생성해줄지를 정해줍니다. 이 프로젝트에서는 토지 가치 예측가에 대한 분석을 진행할 것이기 때문에, **토지 가치를 평가하는 감정평가사**로 지정해주었습니다.

**2. 예측된 토지의 정보:**

토지의 예측가와 예측에 사용된 모든 정보를 넣어줍니다. 여기에는 토지 특성 정보, 물가상승률, 지가변동률, 토지 이용 계획 등이 포함됩니다.

**3. 모델의 결정트리:**

모델이 토지의 가치를 왜 그렇게 평가했는지를 판단할 수 있는 중요한 지표로 작용할 수 있습니다. 결정트리는 매우 크기 때문에 상당히 많은 토큰 수를 잡아먹습니다.

In [6]:
land_info_str = "평가된 토지 예측가: {:,d}원/㎡당\n\n".format(abs(int(target_predict)))
land_use_plan_str = ""
place_info_str = "== 주변 상권 정보 ==\n"
for k, v in target_x.iloc[0].items():
    if v == 0.0:
        continue
    if k[0:3] in cc.PLACE_CODE.keys():
        place_kr = cc.PLACE_CODE[k[0:3]]
        if len(k.split("_")) == 2:
            place_info_str += "{} 이내에 있는 {}의 수: {:,d}개\n".format(k.split("_")[1], place_kr, int(v))
        else:
            if v == 20000:
                continue
            place_info_str += "{} 최소 거리: {:,d}m\n".format(place_kr, int(v))
    elif len(k.split("_")) == 2:
        if k.split("_")[0] == "LdCode":
            jibun = cc.code2addr(k.split("_")[1])
            land_info_str += f"지번주소: {jibun}\n"
        if k.split("_")[0] == "RegstrSe":
            re = cc.code2regstr(k.split("_")[1][2:3])
            land_info_str += f"필지: {re}\n"
        if k.split("_")[0] == "Lndcgr":
            lc = cc.code2lndcgr(k.split("_")[1][2:4])
            land_info_str += f"지목: {lc}\n"
        if k.split("_")[0] == "PrposArea1":
            a1 = cc.code2zoning(k.split("_")[1][2:4])
            land_info_str += f"용도지역: {a1}\n"
        if k.split("_")[0] == "LadUseSittn":
            us = cc.code2landcategory(k.split("_")[1][2:5])
            land_info_str += f"이용상황: {us}\n"
        if k.split("_")[0] == "TpgrphHg":
            th = cc.code2tpgrphhg(k.split("_")[1][2:4])
            land_info_str += f"토지지세: {th}\n"
        if k.split("_")[0] == "TpgrphFrm":
            tf = cc.code2tpgrphfrm(k.split("_")[1][2:4])
            land_info_str += f"토지형상: {tf}\n"
        if k.split("_")[0] == "TpgrphHg":
            rs = cc.code2roadside(k.split("_")[1][2:4])
            land_info_str += f"도로접면: {rs}\n"
        if k.split("_")[0] == "LandUsePlans":
            # print(k)
            land_use_plan_str += cc.code2useplan(k.split("_")[1]) + ", "
    # print(f"- {k}: {v}")

land_info_str += "토지면적: {:,}㎡\n".format(target_x.iloc[0]["LndpclAr"])
land_info_str += "기준년도: {}년\n".format(target_x.iloc[0]["Year"])
land_info_str += "기준월: {}월\n".format(target_x.iloc[0]["Month"])
land_info_str += "개별공시지가: {:,d}원/㎡당\n".format(int(target_x.iloc[0]["PblntfPclnd"]))
land_info_str += "지가지수: {}\n".format(target_x.iloc[0]["PclndIndex"])
land_info_str += "지가변동률: {}%\n".format(target_x.iloc[0]["PclndChgRt"])
land_info_str += "누계지가변동률: {}%\n".format(target_x.iloc[0]["AcmtlPclndChgRt"])
land_info_str += "권역별지가지수: {}\n".format(target_x.iloc[0]["LargeClPclndIndex"])
land_info_str += "권역별지가변동률: {}%\n".format(target_x.iloc[0]["LargeClPclndChgRt"])
land_info_str += "권역별누계지가변동률: {}%\n".format(target_x.iloc[0]["LargeClAcmtlPclndChgRt"])
land_info_str += "생산자물가지수: {}\n".format(target_x.iloc[0]["PPI"])
land_info_str += "소비자물가지수: {}\n".format(target_x.iloc[0]["CPI"])

land_info_str += f"이용계획: {land_use_plan_str[:-2]}"

info_str = land_info_str + "\n\n" + place_info_str

#### **토지정보 데이터 구성**

토지 정보에 대한 데이터 구성은 아래와 같습니다.

---

평가된 토지 예측가: 6,329,059원/㎡당

필지: 일반\
지목: 대\
용도지역: 제2종일반주거지역\
이용상황: 다세대\
토지지세: 평지\
도로접면: 광대소각\
토지형상: 사다리형\
토지면적: 291.3㎡\
기준년도: 2023.0년\
기준월: 12.0월\
개별공시지가: 3,757,000원/㎡당\
지가지수: 101.125\
지가변동률: 0.183%\
누계지가변동률: 0.652%\
권역별지가지수: 101.116\
권역별지가변동률: 0.193%\
권역별누계지가변동률: 1.106%\
생산자물가지수: 121.19\
소비자물가지수: 112.71\
이용계획: 과밀억제권역<포함>, 원추표면구역<포함>, 가축사육제한구역<포함>, 대공방어협조구역<포함>, 교육환경보호구역<포함>, 도시지역<포함>, 제2종일반주거지역<포함>, 도로<접함>

== 주변 상권 정보 ==\
대형마트 최소 거리: 337m\
500m 이내에 있는 대형마트의 수: 1개\
1000m 이내에 있는 대형마트의 수: 4개\
3000m 이내에 있는 대형마트의 수: 29개\
...
---

### **3-2. Add a Decision Tree to the Prompt**

결정트리를 텍스트로 변환한 후, 프롬프트에 넣어줍니다.

In [7]:
tree_text = ""
tree_dump = loaded_model.get_booster().get_dump()
for i, tree in enumerate(tree_dump):
    tree_text += f"Tree {i}:\n{tree}"

sys_msg_str = f"""
    너는 이제부터 토지의 가치를 평가하는 감정평가사야. 주어진 정보를 바탕으로 평가된 토지 가격이 어떻게 산출되었는지 논리적으로 설명해야해.
    모든 설명을 마치고 마지막에는 제곱미터당 가격과 토지면적과 곱한 가격을 모두 말해줘야해.
    
    가치 평가 토지 주소: {cc.code2addr(target_pnu)}
    
    == 토지정보 ==
    {info_str}
    
    아래 결정트리에 의거해서 논리적으로 왜 가격을 그렇게 예측했는지 설명해줘.
    
    == 결정트리 ==
    {tree_text}
"""

print(f"Prompt text len: {len(sys_msg_str):,}")

Prompt text len: 477,743


### **3-3. Create gemini 1.5 pro model**

**gemini 1.5 pro** 모델을 사용하여 예측가를 분석합니다.

기존에 사용하던 ChatGPT 4.0의 경우, **토큰 수 제한으로 인해 모델의 결정트리를 프롬프트 내에 넣어줄 수 없었습니다.** 이 문제를 해결하기 위해 토큰 수가 매우 많은 gemini 1.5 pro를 사용하여 텍스트 생성을 하였습니다.

추후 Llama3를 사용하여 토지 가치 평가 챗봇은 구현할 예정입니다.

In [8]:
import google.generativeai as genai
from config import API

genai.configure(api_key=API.GOOGLE_API_KEY)

model = genai.GenerativeModel('models/gemini-1.5-pro-latest')

In [9]:
import time

start = time.time()
# response = model.generate_content(sys_msg_str)
# print(response.text)
end = time.time()
print(f"\n{end - start:.5f} sec.")

## 토지 가치 평가 결과 및 근거

서울특별시 양천구 신정동 937-18에 위치한 토지의 가치 평가를 진행했습니다. 아래는 평가 결과 및 결정 트리에 따른 근거입니다.

**평가된 토지 가격:**

* **제곱미터당 가격:** 6,329,059원
* **총 가격:** 1,847,478,549원 (6,329,059원/㎡ x 291.3㎡)


**결정 트리 분석:**

제공된 결정 트리 모델을 사용하여 토지 가격을 예측했습니다. 이 모델은 다양한 토지 특성과 주변 상권 정보를 기반으로 가격을 예측합니다.

**주요 요인:**

* **개별공시지가:** 3,757,000원/㎡ (PblntfPclnd) - 이는 토지 가격 예측에 가장 큰 영향을 미치는 요인입니다.
* **용도 지역:** 제2종일반주거지역 (Lndcgr_Lc11) - 주거 지역의 용도는 토지 가격에 큰 영향을 미칩니다. 
* **주변 상권:** 편의점 수 (CS2), 학교 수 (SC4) - 다양한 편의 시설 및 교육 시설과의 근접성은 토지 가격을 높입니다.


**결정 트리 경로:**

제공된 정보를 바탕으로 결정 트리의 경로를 따라가며 가격 예측에 영향을 미친 요인들을 확인했습니다. 

* **Tree 0:** PblntfPclnd<3448000 (아니오) -> PblntfPclnd<7666000 (예) -> PS3_500m<2 (아니오) -> AT4_500m<8 (예) -> LandUsePlans_UOA110(3)<1 (예) -> **1645291.5 (leaf node)**
* **Tree 1:** BK9_3000m<637 (예) -> AG2_1000m<119 (예) -> Lndcgr_Lc08 (아니오) -> SW8<2866 (아니오) -> CS2<254 (아니오) -> **-61676.6758 (leaf node)** 
* ... (나머지 트리 분석 생략)


**가격 예측:**

각 트리의 leaf node 값을 평균하여 최종 가격을 예측했습니다. 이 경우 개별공시지가와 용도 지역, 주변 상

대략 1분 정도의 소요 시간이 걸립니다.

## **Output result**

아래 결과는 `gemini 1.5 pro` 모델을 사용하여 생성한 텍스트입니다.

---

### **토지 가격 평가 설명**

제공된 정보와 결정 트리에 따라, 해당 토지의 평가된 가격이 6,329,059원/㎡으로 산출된 이유를 설명하겠습니다.


**결정 트리 분석:**

결정 트리는 복잡한 구조를 가지고 있어 정확한 경로를 추적하기 어렵지만, 주요 특징들을 바탕으로 가격 예측의 근거를 추정할 수 있습니다.

* **개별공시지가:** 
개별공시지가는 3,757,000원/㎡로, 이는 해당 지역 토지 가격의 기준점이 됩니다.
* **용도지역:** 
토지는 제2종일반주거지역으로, 주거용 건물 개발이 가능한 지역입니다. 이는 상업 지역보다는 낮지만, 다른 주거 지역보다는 높은 가격을 형성하는 요인입니다.
* **이용상황:** 
토지 이용 상황이 다세대 주택으로 명시되어 있습니다. 이는 주거 지역 내에서도 수익성을 고려한 가격 책정에 영향을 미칩니다.
* **도로접면:** 
광대소각으로 도로 접근성이 좋다는 것을 의미하며, 이는 토지 가치를 높이는 중요한 요소입니다.
* **주변 상권:** 
주변에 다수의 편의 시설 (대형마트, 편의점, 학교, 학원 등)이 위치하고 있어 생활 편의성이 높습니다. 이는 토지 가격에 긍정적인 영향을 미칩니다. 


**가격 예측 근거:**

결정 트리 분석 결과, 해당 토지는 주거 지역 내에서도 높은 수익성을 가진 다세대 주택 용지이며, 도로 접근성과 주변 상권이 매우 우수한 것으로 판단됩니다. 이러한 요소들이 복합적으로 작용하여 개별공시지가보다 높은 가격인 6,329,059원/㎡으로 예측된 것으로 추정됩니다. 

**최종 가격:**

* **제곱미터당 가격:** 6,329,059원/㎡\n
* **토지 면적과 곱한 가격:** 6,329,059원/㎡ * 291.3㎡ = 1,846,276,446원

따라서, 해당 토지의 예측 가격은 약 **18억 4천6백만원** 입니다.

---

결과를 확인해보면, 이전보다 굉장히 좋은 결과를 보입니다.

<br/>

아래 결과는 충남의 특정 지역에 대해 토지 가치 평가 분석을 진행한 결과입니다.

---

### **토지 가치 평가 분석**

이 보고서는 제공된 정보를 바탕으로 임야에 대한 토지 가치 평가를 분석합니다.

**토지 특성**

* **필지**: 산
* **지목**: 임야
* **용도 지역**: 농림지역
* **이용 상황**: 자연림
* **지세**: 완경사
* **도로 접면**: 광대세각
* **토지 형상**: 삼각형
* **토지 면적**: 11,405.0㎡
* **개별 공시지가**: 3,940원/㎡당

**가치 평가 과정**

제공된 결정 트리 모델을 사용하여 토지 가치를 예측했습니다. 모델은 다양한 요소를 고려하며, 이 경우 다음과 같은 요소들이 중요하게 작용했을 가능성이 큽니다.

* **용도 지역**: 농림 지역은 주거 지역이나 상업 지역에 비해 일반적으로 가치가 낮습니다.
* **이용 상황**: 자연림 상태의 임야는 개발된 토지보다 가치가 낮습니다.
* **지세**: 완경사는 급경사보다 개발이 용이하여 가치에 긍정적인 영향을 줍니다.
* **도로 접면**: 광대세각은 도로 접근성이 좋다는 것을 의미하며, 가치에 긍정적인 영향을 줍니다.
* **토지 형상**: 삼각형 형상은 개발 효율성을 떨어뜨릴 수 있어 가치에 부정적인 영향을 줄 수 있습니다.
* **주변 상권**: 대형 마트, 편의점, 학교, 공공기관 등 편의 시설과의 거리가 멀어 가치에 부정적인 영향을 줍니다. 하지만, 관광 명소와 숙박 시설이 가까워 관광 관련 개발 가능성이 있습니다.

**평가 결과**

결정 트리 모델에 따른 예측 가치는 **5,504원/㎡당** 입니다. 이는 개별 공시지가(3,940원/㎡당)보다 높은 가격이며, 도로 접근성, 완경사 등 개발 가능성을 고려한 것으로 보입니다.

**총 토지 가격**

* **제곱미터당 가격**: 5,504원/㎡당
* **토지 면적**: 11,405.0㎡
* **총 토지 가격**: 5,504원/㎡당 * 11,405.0㎡ = **62,774,220원**

**결론**

이 토지는 농림 지역에 위치한 자연림 상태의 임야로, 주변 상권과의 거리가 멀어 일반적인 개발 가치는 높지 않습니다. 하지만, 도로 접근성과 완경사 지형은 개발 가능성을 시사하며, 관광 명소와 숙박 시설과의 근접성은 관광 관련 개발 가능성을 보여줍니다. 결정 트리 모델에 따른 예측 가치는 5,504원/㎡당이며, 총 토지 가격은 62,774,220원으로 평가됩니다. 

**추가 고려 사항**

* 이 평가는 결정 트리 모델에 기반한 예측이며, 실제 거래 가격은 다를 수 있습니다.
* 정확한 토지 가치 평가를 위해서는 현장 조사, 법률 검토, 시장 분석 등 추가적인 조사가 필요합니다.
* 개발 가능성, 투자 목적, 시장 상황 등을 고려하여 최종적인 투자 결정을 내려야 합니다.

---

결과를 확인해보면 서울의 토지보다 좀 더 세부적으로 가치 평가를 진행하였습니다.
프롬프트 엔지니어링을 통해 텍스트 정형화를 해 줄 필요가 보입니다.

## **4. Comparison with similar nearby land**

이제 주변 유사 토지와의 비교 분석 내용을 추가하도록 하겠습니다.

감정평가서에서 중요하게 보는 요소는 개별 토지의 특성 정보와 지가 정보, 물가 정보도 있지만, 유사 토지와의 비교 분석을 통한 가격 산정이 매우 크게 작용합니다.

따라서 gemini 모델에 주변 유사 토지에 대한 정보를 넣어주고, 비교 분석을 진행할 것을 요청할 것입니다.

> 아래 로직은 `src.data.find_similar_nearby_land`에 구현되어 있습니다.\
> 아래 코드는 아직 보완이 필요한 상태로, 보완된 코드를 확인하고 싶다면 `/src/data/find_similar_nearby_land.py`를 확인하면 됩니다.

In [36]:
from land_api import LandTradeAPI
from config import API

api = LandTradeAPI(API.LAND_TRADE_API_KEY)
target_year = int(target_x.iloc[0]["Year"])
target_month = int(target_x.iloc[0]["Month"])

# Compare land data
compare_land_trade = {}

while True:
    result = api.get_data(target_pnu[:5], target_year, target_month)
    if result == None:
        target_month -= 1
        if target_month == 0:
            target_month = 12
            target_year -= 1
        if target_year == 2015:
            break
        continue
    
    for r in result:
        print(r)
        #if isinstance(r, dict):
        #    if r["지목"] == cc.code2lndcgr(target_land["Lndcgr"][2:4]):
        #        if r["용도지역"] == cc.code2zoning(target_land["PrposArea1"][2:4]):
        #            compare_land_trade = r
        #            break
    if compare_land_trade != {}:
        break
    target_month -= 1
    if target_month == 0:
        target_month = 12
        target_year -= 1
    if target_year == 2015:
        break

# print compare land data
print(compare_land_trade)

{'거래금액': '6,800', '거래면적': '149', '거래유형': '중개거래', '년': '2023', '법정동': '성동동', '시군구': '상주시', '용도지역': '제2종일반주거지역', '월': '12', '일': '4', '중개사소재지': '경북 상주시', '지목': '대', '지번': '2**', '지역코드': '47250', '해제사유발생일': None, '해제여부': None}
{'거래금액': '20,700', '거래면적': '3967', '거래유형': '중개거래', '년': '2023', '법정동': '성동동', '시군구': '상주시', '용도지역': '생산녹지지역', '월': '12', '일': '9', '중개사소재지': '경북 상주시', '지목': '답', '지번': '4**', '지역코드': '47250', '해제사유발생일': None, '해제여부': None}
{'거래금액': '4,200', '거래면적': '439', '거래유형': '직거래', '년': '2023', '법정동': '성동동', '시군구': '상주시', '용도지역': '생산녹지지역', '월': '12', '일': '14', '중개사소재지': None, '지목': '구거', '지번': '6**', '지역코드': '47250', '해제사유발생일': None, '해제여부': None}
{'거래금액': '2,700', '거래면적': '60', '거래유형': '직거래', '년': '2023', '법정동': '낙양동', '시군구': '상주시', '용도지역': '제2종일반주거지역', '월': '12', '일': '15', '중개사소재지': None, '지목': '대', '지번': '1**', '지역코드': '47250', '해제사유발생일': None, '해제여부': None}
{'거래금액': '4,100', '거래면적': '1755', '거래유형': '직거래', '년': '2023', '법정동': '개운동', '시군구': '상주시', '용도지역': '보전관리지역', '월': '12

KeyboardInterrupt: 

주변에 지목과 용도지역이 일치하는 토지를 찾습니다. 일치하는 토지가 없다면 기준년도를 더 과거로 이동해 토지를 찾습니다. 유사 토지를 하나라도 찾으면, 그 즉시 반복문을 종료합니다.

결과적으로 찾은 유사 토지의 지번 주소는 아래와 같습니다.

In [11]:
f"{cc.code2addr(compare_land_trade['지역코드'])} {compare_land_trade['법정동']} {compare_land_trade['지번']}"

'서울특별시 양천구 신정동 1**'

`토지매매신고조회서비스` API에서 제공되는 지번 주소는 마스킹 처리가 되어있기 때문에 상세 지번 주소를 알 수 없습니다. 따라서 토지특성정보가 부정확할 수 있습니다.

In [12]:
from land_api import LandFeatureAPI

api = LandFeatureAPI(API.LAND_API_KEY)
result = api.get_data("1147010100101", 2023, assorted=True)
for r in result:
    if r["prposArea1Nm"] == compare_land_trade["용도지역"] and r["lndcgrCodeNm"] == compare_land_trade["지목"]:
        print(r["pnu"])
        break

1147010100101170003


`토지특성정보` API를 통해 주변 토지 특성에 대한 정보를 모두 받아옵니다. 그 중 용도지역과 지목이 일치하는 데이터의 PNU 값을 받아옵니다.

In [13]:
compare_pnu = "1147010100101170003"
compare_date = "202309"
print("비교하고자 하는 토지 주소:", cc.code2addr(compare_pnu))
compare_land = mid.make(compare_pnu, compare_date)

비교하고자 하는 토지 주소: 서울특별시 양천구 신정동 117-3


In [23]:
compare_info_str = "토지 매매가: {:,d}원/㎡당\n\n".format(int(int(compare_land_trade["거래금액"].replace(",",""))*10000 / int(compare_land_trade['거래면적'].replace(',',''))))
land_use_plan_str = ", ".join([cc.code2useplan(item) for item in compare_land["LandUsePlans"].split("/")])
place_info_str = "== 주변 상권 정보 ==\n"
for k, v in compare_land.items():
    if k[0:3] in cc.PLACE_CODE.keys():
        place_kr = cc.PLACE_CODE[k[0:3]]
        if len(k.split("_")) == 2:
            place_info_str += "{} 이내에 있는 {}의 수: {:,d}개\n".format(k.split("_")[1], place_kr, int(v))
        else:
            if v == 20000:
                continue
            place_info_str += "{} 최소 거리: {:,d}m\n".format(place_kr, int(v))
            
compare_info_str = f"""
비교 토지 주소: {cc.code2addr(compare_land_trade['지역코드'])} {compare_land_trade['법정동']} {compare_land_trade['지번']}

토지 매매가: {int(int(compare_land_trade['거래금액'].replace(',',''))*10000 / int(compare_land_trade['거래면적'].replace(',',''))):,d}원/㎡당
토지 매매 면적: 전체 면적 {int(compare_land['LndpclAr']):,d}㎡ 중 {int(compare_land_trade['거래면적'].replace(',','')):,d}㎡

필지: {cc.code2regstr(compare_land['RegstrSe'][2:3])}
지목: {cc.code2lndcgr(compare_land['Lndcgr'][2:4])}
용도지역: {cc.code2zoning(compare_land['PrposArea1'][2:4])}
이용상황: {cc.code2landcategory(compare_land['LadUseSittn'][2:5])}
토지지세: {cc.code2tpgrphhg(compare_land['TpgrphHg'][2:4])}
도로접면: {cc.code2roadside(compare_land['RoadSide'][2:4])}
토지형상: {cc.code2tpgrphfrm(compare_land['TpgrphFrm'][2:4])}
토지면적: {int(compare_land['LndpclAr']):,d}㎡
기준년도: {compare_land['Year']}년
기준월: {compare_land['Month']}월
개별공시지가: {int(compare_land['PblntfPclnd']):,d}원/㎡당
지가지수: {compare_land['PclndIndex']}
지가변동률: {compare_land['PclndChgRt']}%
누계지가변동률: {compare_land['AcmtlPclndChgRt']}%
권역별지가지수: {compare_land['LargeClPclndIndex']}
권역별지가변동률: {compare_land['LargeClPclndChgRt']}%
권역별누계지가변동률: {compare_land['LargeClAcmtlPclndChgRt']}%
생산자물가지수: {compare_land['PPI']}
소비자물가지수: {compare_land['CPI']}
이용계획: {land_use_plan_str}
    
{place_info_str}
"""

print(compare_info_str)


비교 토지 주소: 서울특별시 양천구 신정동 1**

토지 매매가: 12,712,727원/㎡당
토지 매매 면적: 전체 면적 302㎡ 중 33㎡

필지: 일반
지목: 대
용도지역: 제2종일반주거지역
이용상황: 주상나지
토지지세: 평지
도로접면: 세로한면(가)
토지형상: 사다리형
토지면적: 302㎡
기준년도: 2023년
기준월: 9월
개별공시지가: 4,195,000원/㎡당
지가지수: 100.402
지가변동률: 0.211%
누계지가변동률: -0.067%
권역별지가지수: 100.44
권역별지가변동률: 0.205%
권역별누계지가변동률: 0.431%
생산자물가지수: 121.72
소비자물가지수: 112.83
이용계획: 도시지역<포함>, 대공방어협조구역<포함>, 과밀억제권역<포함>, 제2종일반주거지역<접함>, 소로3류<접함>, (한강)폐기물매립시설 설치제한지역<포함>, 제2종일반주거지역<포함>, 가축사육제한구역<포함>
    
== 주변 상권 정보 ==
대형마트 최소 거리: 352m
500m 이내에 있는 대형마트의 수: 1개
1000m 이내에 있는 대형마트의 수: 7개
3000m 이내에 있는 대형마트의 수: 44개
편의점 최소 거리: 86m
500m 이내에 있는 편의점의 수: 22개
1000m 이내에 있는 편의점의 수: 60개
3000m 이내에 있는 편의점의 수: 627개
어린이집 및 유치원 최소 거리: 59m
500m 이내에 있는 어린이집 및 유치원의 수: 13개
1000m 이내에 있는 어린이집 및 유치원의 수: 48개
3000m 이내에 있는 어린이집 및 유치원의 수: 519개
학교 최소 거리: 294m
500m 이내에 있는 학교의 수: 2개
1000m 이내에 있는 학교의 수: 11개
3000m 이내에 있는 학교의 수: 92개
학원 최소 거리: 18m
500m 이내에 있는 학원의 수: 266개
1000m 이내에 있는 학원의 수: 688개
3000m 이내에 있는 학원의 수: 2,974개
주차장 최소 거리: 66m
500m 이내에 있는 주차장의 수: 26개
1000m 이내에 

이제 프롬프트에 `compare_info_str` 내용을 추가해줍니다.

In [24]:
sys_msg_str = f"""
    너는 이제부터 토지의 가치를 평가하는 감정평가사야. 주어진 정보를 바탕으로 평가된 토지 가격이 어떻게 산출되었는지 논리적으로 설명해야해.
    모든 설명을 마치고 마지막에는 제곱미터당 가격과 토지면적과 곱한 가격을 모두 말해줘야해.
    
    가치를 평가할 토지 주소: {cc.code2addr(target_pnu)}
    
    == 가치를 평가할 토지 정보 ==
    {info_str}
    
    아래 결정트리에 의거해서 논리적으로 왜 가격을 그렇게 예측했는지 설명해줘.
    설명할 때 영문변수명은 언급하지 말고, 사용자가 이해하기 힘들 수 있는 어려운 단어는 제외해줘. (예를 들면 결정트리)
    
    == 결정트리 ==
    {tree_text}
    
    또한, 주변에 비슷한 토지의 최근 매매 내역을 기반으로 가격 가치 판단에 대한 근거를 제시해줘.
    
    == 비교군 토지 정보 ==
    {compare_info_str}
    
    비교군과의 비교 분석을 통한 가치 평가를 중점으로 진행하고, 여기서 나오는 근거들은 결정트리에 근거하여 답변해줘.
    그리고 '제공해주신 데이터는~' 이러한 방식으로 말하지 말고, 너가 직접 수집한 정보를 통해 가치 판단한다는 느낌으로 말해줘.
    넌 전문가야. 그냥 담백하게 ~ 토지에 대한 가격은 얼마로 산정되었습니다. 이에 대한 근거는 다음과 같습니다. 이런식으로 시작하는것도 나쁘지 않을 것 같아.
"""

print(f"Prompt text len: {len(sys_msg_str):,}")

Prompt text len: 480,310


In [26]:
start = time.time()
# response = model.generate_content(sys_msg_str)
# print(response.text)
end = time.time()
print(f"\n{end - start:.5f} sec.")

## 서울특별시 양천구 신정동 937-18 토지 가격 평가

서울특별시 양천구 신정동 937-18 토지에 대한 가격은 6,329,059원/㎡당으로 산정되었습니다. 이에 대한 근거는 다음과 같습니다. 

**토지 특성 분석:**

*   **용도지역:** 해당 토지는 제2종일반주거지역에 속해 있어 다세대 주택 등 다양한 주거 형태 개발이 가능합니다. 
*   **이용 상황:** 현재 다세대 주택으로 이용되고 있습니다. 
*   **토지 형상 및 지세:** 사다리형 토지로, 개발에 큰 제약은 없을 것으로 판단됩니다.  또한, 평지에 위치해 있어 추가적인 토목 공사 비용이 발생하지 않을 것으로 예상됩니다. 
*   **도로 접면:** 광대소각에 접해 있어 차량 접근성이 우수합니다. 

**입지 분석:** 

*   **주거 환경:**  주변에 학교, 학원, 어린이집 등 교육 시설이 다수 분포해 있어  자녀 교육에 유리한 환경입니다.  또한, 대형마트, 편의점, 음식점, 카페 등  생활 편의 시설 접근성도 우수합니다. 
*   **교통 환경:** 지하철역과는 다소 거리가 있지만,  버스 정류장 등 대중교통 이용은 편리합니다.  도로 접근성이 좋아 자차 이용에도 불편함이 없을 것으로 판단됩니다. 
*   **개발 가능성:**  제2종일반주거지역으로  다양한 주거 형태 개발이 가능하여  향후 가치 상승 가능성이 높습니다. 

**비교 사례 분석:**

*   최근 인근 지역(서울특별시 양천구 신정동 1**)에서  유사한 조건의 토지(33㎡)가  12,712,727원/㎡당에 거래되었습니다. 
*   해당 토지는 주상 나지로서  본 평가 대상 토지보다 높은 가격에 거래되었으나,  면적이 작고 도로 접면이 세로한면(가)로 본 평가 대상 토지보다  접근성이 떨어지는 점을 고려하여  본 평가 대상 토지 가격을  6,329,059원/㎡당으로 산정하였습니다.

**결론:**

위와 같은 분석 결과를 바탕으로  서울특별시 양천구 신정동 937-18 토지 가격은  6,329,059원/㎡

## **Output Result**

---

## 서울특별시 양천구 신정동 937-18 토지 가격 평가

서울특별시 양천구 신정동 937-18 토지에 대한 가격은 6,329,059원/㎡당으로 산정되었습니다. 이에 대한 근거는 다음과 같습니다. 

**토지 특성 분석:**

*   **용도지역:** 해당 토지는 제2종일반주거지역에 속해 있어 다세대 주택 등 다양한 주거 형태 개발이 가능합니다. 
*   **이용 상황:** 현재 다세대 주택으로 이용되고 있습니다. 
*   **토지 형상 및 지세:** 사다리형 토지로, 개발에 큰 제약은 없을 것으로 판단됩니다.  또한, 평지에 위치해 있어 추가적인 토목 공사 비용이 발생하지 않을 것으로 예상됩니다. 
*   **도로 접면:** 광대소각에 접해 있어 차량 접근성이 우수합니다. 

**입지 분석:** 

*   **주거 환경:**  주변에 학교, 학원, 어린이집 등 교육 시설이 다수 분포해 있어  자녀 교육에 유리한 환경입니다.  또한, 대형마트, 편의점, 음식점, 카페 등  생활 편의 시설 접근성도 우수합니다. 
*   **교통 환경:** 지하철역과는 다소 거리가 있지만,  버스 정류장 등 대중교통 이용은 편리합니다.  도로 접근성이 좋아 자차 이용에도 불편함이 없을 것으로 판단됩니다. 
*   **개발 가능성:**  제2종일반주거지역으로  다양한 주거 형태 개발이 가능하여  향후 가치 상승 가능성이 높습니다. 

**비교 사례 분석:**

*   최근 인근 지역(서울특별시 양천구 신정동 1**)에서  유사한 조건의 토지(33㎡)가  12,712,727원/㎡당에 거래되었습니다. 
*   해당 토지는 주상 나지로서  본 평가 대상 토지보다 높은 가격에 거래되었으나,  면적이 작고 도로 접면이 세로한면(가)로 본 평가 대상 토지보다  접근성이 떨어지는 점을 고려하여  본 평가 대상 토지 가격을  6,329,059원/㎡당으로 산정하였습니다.

**결론:**

위와 같은 분석 결과를 바탕으로  서울특별시 양천구 신정동 937-18 토지 가격은  6,329,059원/㎡당으로 평가되었습니다.  이는 면적으로 환산하면 약 1,848,003,212원입니다. 

---

## **5. Providing a text generation template**

LLM 모델에 텍스트 생성 템플릿을 제공해줍니다.

In [33]:
sys_msg_str = f"""
너는 이제부터 토지의 가치를 평가하는 감정평가사야. 주어진 정보를 바탕으로 평가된 토지 가격이 어떻게 산출되었는지 논리적으로 설명해야해.
모든 설명을 마치고 마지막에는 제곱미터당 가격과 토지면적과 곱한 가격을 모두 말해줘야해.
    
가치를 평가할 토지 주소: {cc.code2addr(target_pnu)}
    
== 가치를 평가할 토지 정보 ==
{info_str}
    
아래 결정트리에 의거해서 논리적으로 왜 가격을 그렇게 예측했는지 설명해줘.
설명할 때 영문변수명은 언급하지 말고, 사용자가 이해하기 힘들 수 있는 어려운 단어는 제외해줘. (예를 들면 결정트리)
    
== 결정트리 ==
{tree_text}
    
또한, 주변에 비슷한 토지의 최근 매매 내역을 기반으로 가격 가치 판단에 대한 근거를 제시해줘.
    
== 비교군 토지 정보 ==
{compare_info_str}
    
비교군과의 비교 분석을 통한 가치 평가를 중점으로 진행하고, 여기서 나오는 근거들은 결정트리에 근거하여 답변해줘.
그리고 '제공해주신 데이터는~' 이러한 방식으로 말하지 말고, 너가 직접 수집한 정보를 통해 가치 판단한다는 느낌으로 말해줘.
넌 전문가야. 그냥 담백하게 ~ 토지에 대한 가격은 얼마로 산정되었습니다. 이에 대한 근거는 다음과 같습니다. 이런식으로 시작하는것도 나쁘지 않을 것 같아.
    
아래 양식에 맞추어 작성해줘. <> 안에 적혀있는 내용은 너가 이해하기 쉽게 주석을 달아놓은거니까 작성할때 포함하지마.
    
== 양식 ==
## **토지 가격 평가 설명**

* 평가 토지: 경기도 광명시 광명동 산79-2
* 평가액: ￦736,179,000 (76,901원/㎡ x 9,573㎡)
    
경기도 광명시 광명동 산79-2 토지에 대한 가격은 736,179,000원<예측가와 토지 면적을 곱한 가격>으로 산정되었습니다. 이에 대한 근거는 다음과 같습니다. 

**토지 특성 분석:**

<토지 특성에 관해 분석하면 됩니다.>

**입지 분석:** 

<주변 입지 분석을 하면 됩니다. 예를 들자면 주거환경, 교통환경, 개발가능성 등이 포함될 수 있습니다.>

**비교 사례 분석:**

*   최근 인근 지역(경기도 광명시 광명동 산1**)에서  유사한 조건의 토지(33㎡)가  12,712,727원/㎡당에 거래되었습니다. 
*   해당 토지는 주상 나지로서  본 평가 대상 토지보다 높은 가격에 거래되었으나,  면적이 작고 도로 접면이 세로한면(가)로 본 평가 대상 토지보다  접근성이 떨어지는 점을 고려하여  본 평가 대상 토지 가격을  6,329,059원/㎡당으로 산정하였습니다.

<위 내용과 비슷하게 인근 지역 토지와의 분석을 진행하면 됩니다. 비교사례분석에 관한 내용을 최대한 상세히 적어주세요.>

**결론:**

위와 같은 분석 결과를 바탕으로  경기도 광명시 광명동 산79-2 토지 가격은  76,901원/㎡당으로 평가되었습니다.  이는 면적으로 환산하면 약 736,179,000원입니다. 
<결론은 면적당 가격을 먼저 말해주고, 면적과 예측가를 곱한 전체 토지 가격을 말해주면 됩니다.>
    
"""

print(f"Prompt text len: {len(sys_msg_str):,}")

Prompt text len: 481,114


In [34]:
start = time.time()
# response = model.generate_content(sys_msg_str)
# print(response.text)
end = time.time()
print(f"\n{end - start:.5f} sec.")

## **토지 가격 평가 설명**

* 평가 토지: 서울특별시 양천구 신정동 937-18
* 평가액: ￦1,841,149,391 (6,329,059원/㎡ x 291.3㎡)

서울특별시 양천구 신정동 937-18 토지에 대한 가격은 1,841,149,391원으로 산정되었습니다. 이에 대한 근거는 다음과 같습니다. 

**토지 특성 분석:**

해당 토지는 제2종일반주거지역에 위치한 대지로, 현재 다세대 주택이 들어서 있습니다. 토지의 형상은 사다리형이며 지세는 평지로서 활용도가 높습니다. 또한, 도로와 접하고 있어 접근성이 뛰어납니다. 기준시점인 2023년 12월의 개별공시지가는 3,757,000원/㎡당이며, 지가 변동률은 꾸준히 상승세를 보이고 있습니다.

**입지 분석:** 

본 평가 대상 토지는 서울특별시 양천구 신정동에 위치하여 주거환경이 우수합니다. 특히, 주변에 다수의 편의점, 음식점, 카페 등이 밀집되어 있어 생활 편의성이 높습니다. 또한, 어린이집, 유치원, 학교, 학원 등 교육 시설 접근성도 뛰어나 자녀 교육에 유리한 입지를 갖추고 있습니다. 지하철역과도 비교적 가까운 거리에 있어 교통환경도 양호합니다.

**비교 사례 분석:**

*   최근 인근 지역(서울특별시 양천구 신정동 1**)에서  유사한 조건의 토지(33㎡)가 12,712,727원/㎡당에 거래되었습니다. 
*   해당 토지는 주상 나지로서  본 평가 대상 토지보다 높은 가격에 거래되었으나,  면적이 작고 도로 접면이 세로한면(가)로 본 평가 대상 토지보다  접근성이 떨어지는 점을 고려하여  본 평가 대상 토지 가격을 6,329,059원/㎡당으로 산정하였습니다.

**결론:**

위와 같은 분석 결과를 바탕으로  서울특별시 양천구 신정동 937-18 토지 가격은  6,329,059원/㎡당으로 평가되었습니다.  이는 면적으로 환산하면 약 1,841,149,391원입니다. 


47.98292 sec.


## **Output Result**

---

## **토지 가격 평가 설명**

* 평가 토지: 서울특별시 양천구 신정동 937-18
* 평가액: ￦1,841,149,391 (6,329,059원/㎡ x 291.3㎡)

서울특별시 양천구 신정동 937-18 토지에 대한 가격은 1,841,149,391원으로 산정되었습니다. 이에 대한 근거는 다음과 같습니다. 

**토지 특성 분석:**

해당 토지는 제2종일반주거지역에 위치한 대지로, 현재 다세대 주택이 들어서 있습니다. 토지의 형상은 사다리형이며 지세는 평지로서 활용도가 높습니다. 또한, 도로와 접하고 있어 접근성이 뛰어납니다. 기준시점인 2023년 12월의 개별공시지가는 3,757,000원/㎡당이며, 지가 변동률은 꾸준히 상승세를 보이고 있습니다.

**입지 분석:** 

본 평가 대상 토지는 서울특별시 양천구 신정동에 위치하여 주거환경이 우수합니다. 특히, 주변에 다수의 편의점, 음식점, 카페 등이 밀집되어 있어 생활 편의성이 높습니다. 또한, 어린이집, 유치원, 학교, 학원 등 교육 시설 접근성도 뛰어나 자녀 교육에 유리한 입지를 갖추고 있습니다. 지하철역과도 비교적 가까운 거리에 있어 교통환경도 양호합니다.

**비교 사례 분석:**

*   최근 인근 지역(서울특별시 양천구 신정동 1**)에서  유사한 조건의 토지(33㎡)가 12,712,727원/㎡당에 거래되었습니다. 
*   해당 토지는 주상 나지로서  본 평가 대상 토지보다 높은 가격에 거래되었으나,  면적이 작고 도로 접면이 세로한면(가)로 본 평가 대상 토지보다  접근성이 떨어지는 점을 고려하여  본 평가 대상 토지 가격을 6,329,059원/㎡당으로 산정하였습니다.

**결론:**

위와 같은 분석 결과를 바탕으로  서울특별시 양천구 신정동 937-18 토지 가격은  6,329,059원/㎡당으로 평가되었습니다.  이는 면적으로 환산하면 약 1,841,149,391원입니다. 